In [6]:
#!pip install langchain langchain_community langchain_chroma langchain_text_splitters langchain_huggingface sentence-transformers langchain_qdrant qdrant-client langchain_ollama

In [39]:
!pip install langchain langchain_openai

  Using cached openai-1.54.3-py3-none-any.whl.metadata (24 kB)
  Using cached distro-1.9.0-py3-none-any.whl.metadata (6.8 kB)
  Using cached tqdm-4.67.0-py3-none-any.whl.metadata (57 kB)
Using cached openai-1.54.3-py3-none-any.whl (389 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 982.4/982.4 kB 15.5 MB/s eta 0:00:00
Using cached distro-1.9.0-py3-none-any.whl (20 kB)
Using cached tqdm-4.67.0-py3-none-any.whl (78 kB)


### 1) Carga de Datos:
A cada grupo se le asignará un país al azar.
Obtengan la regulación correspondiente al país asignado, en formato PDF o directamente desde el sitio web oficial.
Asegúrense de guardar el archivo de texto procesado o descargado en una carpeta llamada data dentro del repositorio.

1) Load document:
- Import the PyPDFLoader from langchain_community
- Specify the file path
- Create a loader object
- Load the document, which returns a list of Document objects

In [3]:
#ruta particular donde estará el archivo pdf
my_path = "/Users/carloszurita/Documents/GIT/practicos-rag/data/"

In [4]:
from langchain_community.document_loaders import PyPDFLoader
from dotenv import load_dotenv

load_dotenv()

file_path = (
my_path + "biblioteca-de-alimentos.pdf"
)
loader = PyPDFLoader(file_path)
docs = loader.load()
docs[0:2]

[Document(metadata={'source': '/Users/carloszurita/Documents/GIT/practicos-rag/data/biblioteca-de-alimentos.pdf', 'page': 0}, page_content=' \n   \n \n  \nBIBLIOTECA DE  \nALIMENTOS  \nAtualizada em 06.11.202 4 \nCoordenação de Processos Regulatórios – CPROR  \nAssessoria de Melhoria da Qualidade Regulatória – ASREG  \nGabinete do Diretor -Presidente  \n \nAGENDA REGULATÓRIA \nCiclo Bienal  \n2024 -2025  '),
 Document(metadata={'source': '/Users/carloszurita/Documents/GIT/practicos-rag/data/biblioteca-de-alimentos.pdf', 'page': 1}, page_content=' \n APRESENTAÇÃO  \n \n As Bibliotecas são documentos que reúnem todas as normas vigentes de determinado \nmacrotema, divididos por temas. O objetivo é facilitar o acesso e a compreensão do Estoque \nRegulatório ao público interno e externo, bem como aprimorar o processo de elaboração e \nrevisão das normativas.  \n \n \nNão deixe de consultar também a Biblioteca de Temas Transversais , que abrange assuntos \naplicados a todos os macrotemas, ta

In [18]:
#ver pagina 3 del doc
docs[2].page_content

' \n Sumário  \n1. Regularização, avaliação de risco e padrões de alimentos  ................................ ................................ .........................  4 \n1.1. Procedimentos para regularização de alimentos  ................................ ................................ ............................  4 \n1.2. Procedimentos para avaliação de risco, segurança e eficácia de alimentos  ................................ ....................  5 \n1.3. Padrões microbiológicos para alimentos  ................................ ................................ ................................ ........  5 \n1.4. Irradiação de alimentos  ................................ ................................ ................................ ................................ . 6 \n1.5. Procedimentos para autorização de uso de aditivos alimentares e coadjuvantes de tecnologia  .....................  6 \n1.6. Contaminantes em alimentos  ................................ ....................

In [24]:
# Extraer el contenido de texto de cada página en el PDF y unirlo en all_texts 
all_texts = [doc.page_content for doc in docs if hasattr(doc, "page_content")]

### 2) Limpieza de Datos:

Apliquen las técnicas de limpieza vistas en clase para preparar el texto. Esto incluye:
Eliminación de caracteres especiales.
Normalización de texto (conversión a minúsculas, eliminación de acentos, etc.).
Eliminación de palabras irrelevantes (stop words) o la lematización del texto.
Incluyan este proceso en un script Python dentro de la carpeta src, asegurándose de que el código sea reproducible para otros grupos.

In [ ]:
#codigo aca

### 3) Segmentación (Chunking):
Dividan el texto en fragmentos (chunks) aplicando alguna de las técnicas estudiadas (token-level, sentence-level o semantic-level).
Asegúrense de que los fragmentos mantengan un balance entre contexto y precisión para facilitar el proceso de recuperación.
Guardar los datos segmentados dentro de la carpeta data/chunks. 
Incluyan este proceso en un script Python dentro de la carpeta src, asegurándose de que el código sea reproducible para otros grupos.
BONUS: Incluyan algún preprocesamiento adicional que pueda mejorar la calidad del análisis, como 

#### Split into smaller chunks:
- Import the RecursiveCharacterTextSplitter
- Create a splitter object with specified chunk size and overlap
- Split the documents into smaller pieces

In [25]:
from langchain_text_splitters import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(chunk_size=450, chunk_overlap=0)

In [26]:
#splits en pequeños documentos
splits = text_splitter.split_documents(docs)
splits[0:2]

[Document(metadata={'source': '/Users/carloszurita/Documents/GIT/practicos-rag/data/biblioteca-de-alimentos.pdf', 'page': 0}, page_content='BIBLIOTECA DE  \nALIMENTOS  \nAtualizada em 06.11.202 4 \nCoordenação de Processos Regulatórios – CPROR  \nAssessoria de Melhoria da Qualidade Regulatória – ASREG  \nGabinete do Diretor -Presidente  \n \nAGENDA REGULATÓRIA \nCiclo Bienal  \n2024 -2025'),
 Document(metadata={'source': '/Users/carloszurita/Documents/GIT/practicos-rag/data/biblioteca-de-alimentos.pdf', 'page': 1}, page_content='APRESENTAÇÃO  \n \n As Bibliotecas são documentos que reúnem todas as normas vigentes de determinado \nmacrotema, divididos por temas. O objetivo é facilitar o acesso e a compreensão do Estoque \nRegulatório ao público interno e externo, bem como aprimorar o processo de elaboração e \nrevisão das normativas.  \n \n \nNão deixe de consultar também a Biblioteca de Temas Transversais , que abrange assuntos')]

In [27]:
split_recursive_character = text_splitter.create_documents(all_texts)
split_recursive_character

[Document(metadata={}, page_content='BIBLIOTECA DE  \nALIMENTOS  \nAtualizada em 06.11.202 4 \nCoordenação de Processos Regulatórios – CPROR  \nAssessoria de Melhoria da Qualidade Regulatória – ASREG  \nGabinete do Diretor -Presidente  \n \nAGENDA REGULATÓRIA \nCiclo Bienal  \n2024 -2025'),
 Document(metadata={}, page_content='APRESENTAÇÃO  \n \n As Bibliotecas são documentos que reúnem todas as normas vigentes de determinado \nmacrotema, divididos por temas. O objetivo é facilitar o acesso e a compreensão do Estoque \nRegulatório ao público interno e externo, bem como aprimorar o processo de elaboração e \nrevisão das normativas.  \n \n \nNão deixe de consultar também a Biblioteca de Temas Transversais , que abrange assuntos'),
 Document(metadata={}, page_content='aplicados a todos os macrotemas, tais como: Autorização de Funcionamento de Empresa \n(AFE), Certificação de Boas Práticas de Fabricação (CBPF), Taxas de Fiscalização de Vigilância \nSanitária (TFVS), Peticionamento de Recur

In [32]:
#Si no existe se crea la carpeta data/chunks
import os
os.makedirs(my_path + "/chunks", exist_ok=True)

In [34]:
# Guardar cada fragmento en un archivo de texto
for i, chunk in enumerate(split_recursive_character):
    with open(my_path + f"/chunks/chunk_{i + 1}.txt", "w") as f:
        f.write(chunk.page_content)

### 4) Creación de Embeddings:
Generen embeddings para cada chunk utilizando un modelo de embeddings que elijan.
Guarden los embeddings en la carpeta embeddings dentro del repositorio para usarlos en el paso de recuperación.

In [35]:
my_api_key = ''

In [41]:
# Configuración del modelo de embeddings usando la API key almacenada en my_api_key
from langchain.embeddings import OpenAIEmbeddings

embeddings_model = OpenAIEmbeddings(model="text-embedding-3-small", openai_api_key=my_api_key)

/var/folders/2y/w7q6dzmn0xvd8k73mz2tz8f40000gn/T/ipykernel_88858/1173150093.py:4: LangChainDeprecationWarning: The class `OpenAIEmbeddings` was deprecated in LangChain 0.0.9 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-openai package and should be used instead. To use it run `pip install -U :class:`~langchain-openai` and import as `from :class:`~langchain_openai import OpenAIEmbeddings``.
  embeddings_model = OpenAIEmbeddings(model="text-embedding-3-small", openai_api_key=my_api_key)


In [44]:
# setup modelo de embeddings llamando api key  "my_api_key"
oaiembeds = OpenAIEmbeddings(model="text-embedding-ada-002", openai_api_key=my_api_key)

In [45]:
# Obtener todas las frases combinadas
sentences = [{"combined_sentence": chunk.page_content} for chunk in split_recursive_character]

In [46]:
# Generar embeddings para todas las frases combinadas
embeddings = oaiembeds.embed_documents([x['combined_sentence'] for x in sentences])

In [49]:
#visualizamos embeddings
embeddings

[[-0.01288866138379036,
  -0.015247414751419395,
  0.004683713693725811,
  -0.015139277018516167,
  0.0034773028095161436,
  0.011800526377774255,
  0.007853500058129056,
  0.0035955784548790492,
  -0.018653751475225824,
  -0.007988672224258092,
  0.016328792080451675,
  -0.01803196137367752,
  -0.007522328251112921,
  -0.011901904571048404,
  -0.005829297801669384,
  0.009820254143983891,
  0.026669459064032352,
  -0.02438504945645166,
  0.013469901698145211,
  -0.01715334229383879,
  0.003936887941524206,
  0.007414190518209693,
  0.0072114327346774545,
  -0.004146404799024211,
  0.01897816467393551,
  -0.01572051733287102,
  -0.0027608905618629145,
  -0.03111662146703235,
  0.02620987369919363,
  -0.013936245671290383,
  0.00600164184782259,
  -0.0014362037994596843,
  0.015004104852387132,
  -0.004305232094225827,
  0.003105579352661297,
  -0.037604881715935526,
  -0.00700191587717745,
  -0.02143829809748395,
  0.021235539848290394,
  -0.01465265722045164,
  0.005035161325661302,
 

In [47]:
import os
# Crear la carpeta embeddings si no existe
os.makedirs("embeddings", exist_ok=True)

In [48]:
# Cada embedding se guarda a un archivo txt por separado
for i, sentence in enumerate(sentences):
    
    sentence['combined_sentence_embedding'] = embeddings[i]
    
    # Guardar el embedding en un archivo .txt separado
    
    with open(f"embeddings/chunk_{i + 1}_embedding.txt", "w") as f:
        f.write(" ".join(map(str, embeddings[i])))
        

**** hasta aca primera parte ****